## Imports

In [1]:
%load_ext autoreload
%autoreload 2
import sys
sys.path.append('..')
from utils.loading import load_table

import pandas as pd
import plotly.express as px

## Parameters

In [2]:
# Dictionary of 'table_name' -> []'patient', 'datetime']
tables = {
    'Meter': ['DeidentID', 'DataDtTm'],
    'CGM': ['DeidentID', 'DisplayTime'],
    'CGMCal': ['DeidentID', 'DisplayTime'],
    'Ketone': ['DeidentID', 'DataDtTm'],
    'MonitorBasalBolus': ['DeidentID', 'LocalDeliveredDtTm'],
    'MonitorCGM': ['DeidentID', 'LocalDtTm'],
    'MonitorCorrectionBolus': ['DeidentID', 'LocalDeliveredDtTm'],
    'MonitorMeal': ['DeidentID', 'LocalDtTm'],
    'MonitorMealBolus': ['DeidentID', 'LocalDeliveredDtTm'],
    'MonitorSMBG': ['DeidentID','LocalDtTm'],
    'MonitorSystem': ['DeidentID','LocalDtTm'],
    'MonitorTotalBolus': ['DeidentID', 'LocalDeliveredDtTm'],
    'Pump': ['DeidentID', 'DataDtTm'],
}

GROUP_DATES = True

In [3]:
data = pd.DataFrame(columns=['patient', 'time', 'table'])
for table, cols in tables.items():
    print(table)
    t = load_table(filename=table, date_cols=[cols[1]])
    t = t[cols].rename(columns=dict(zip(cols, ['patient', 'time']))).assign(table=table)
    if GROUP_DATES:
        t['time'] = t['time'].dt.date
        t.drop_duplicates(inplace=True)
    data = pd.concat([data, t])


Meter
CGM
CGMCal
Ketone
MonitorBasalBolus


In [ ]:
# IF YOU WANT TO INCLUDE A FILTER COLUMN.
filter_df = pd.read_pickle('filter.df')

data = pd.concat([data, filter_df[filter_df.all_covered]])

In [ ]:
fig = px.scatter(data, x='time', facet_row='table', color='patient', y='patient', category_orders={'patient': [str(x) for x in sorted(data.patient.unique())]})
fig.update_yaxes(visible=False)
for annotation in fig['layout']['annotations']: 
    annotation['textangle']= 0
fig.update_layout(legend={
    'orientation':'h',
}, margin={'r': 200})
fig.show()